Topics: Approximation and Indexing
* Approximation quality
* R-tree

# Chapter 1: Approximation Quality

In [ ]:
!pip install --quiet geojson ipyleaflet turfpy

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 14.9 MB/s eta 0:00:00


Loading the data

In [ ]:
import requests

url1 = "https://raw.githubusercontent.com/isellsoap/deutschlandGeoJSON/refs/heads/main/1_deutschland/1_sehr_hoch.geo.json"
url2 = "https://raw.githubusercontent.com/isellsoap/deutschlandGeoJSON/refs/heads/main/1_deutschland/2_hoch.geo.json"
url3 = "https://raw.githubusercontent.com/isellsoap/deutschlandGeoJSON/refs/heads/main/1_deutschland/3_mittel.geo.json"
url4 = "https://raw.githubusercontent.com/isellsoap/deutschlandGeoJSON/refs/heads/main/1_deutschland/4_niedrig.geo.json"


# source: https://github.com/isellsoap/deutschlandGeoJSON/tree/main/1_deutschland
veryhighres_data = requests.get(url1).json()
highres_data = requests.get(url2).json()
mediumres_data = requests.get(url3).json()
lowres_data = requests.get(url4).json()

print(veryhighres_data)
print(highres_data)
print(mediumres_data)
print(lowres_data)

{'type': 'FeatureCollection', 'features': [{'type': 'Feature', 'id': 0, 'properties': {'ID_0': 86, 'ISO': 'DEU', 'NAME_ENGLI': 'Germany', 'NAME_ISO': 'GERMANY', 'NAME_FAO': 'Germany', 'NAME_LOCAL': 'Deutschland', 'NAME_OBSOL': None, 'NAME_VARIA': 'Germany', 'NAME_NONLA': None, 'NAME_FRENC': 'Allemagne', 'NAME_SPANI': 'Alemania', 'NAME_RUSSI': '????????', 'NAME_ARABI': '???????', 'NAME_CHINE': '??', 'WASPARTOF': None, 'CONTAINS': 'East Germany|West Germany|DDR', 'SOVEREIGN': 'Germany', 'ISO2': 'DE', 'WWW': None, 'FIPS': 'GM', 'ISON': 276.0, 'VALIDFR': 'Unknown', 'VALIDTO': 'Present', 'EUmember': 1.0}, 'geometry': {'type': 'MultiPolygon', 'coordinates': [[[[8.708373069763297, 47.71555709838867], [8.709177970886287, 47.71345901489258], [8.710095405578954, 47.71168518066429], [8.710541725158635, 47.70994949340832], [8.710783958435286, 47.70932006835932], [8.711812019348486, 47.708053588867585], [8.712482452393033, 47.70676803588867], [8.71268272399908, 47.706062316894645], [8.7131071090698

Visualizing the data

In [ ]:
from geojson import Point, Feature
from ipyleaflet import Map, GeoJSON, LayersControl

center = [51.96954, 7.595]

m = Map(center=center, zoom=6)

veryhighres_map = GeoJSON(name="Very high resolution", data=veryhighres_data, style={"color": "red"})
highres_map = GeoJSON(name = "High resolution", data=highres_data , style={"color": "blue"})
mediumres_map = GeoJSON(name = "Medium resolution", data=mediumres_data , style={"color": "green"})
lowres_map = GeoJSON(name = "Low resolution", data=lowres_data)

control = LayersControl(position="topright")
m.add_control(control)

m.add_layer(veryhighres_map)
m.add_layer(highres_map)
m.add_layer(mediumres_map)
m.add_layer(lowres_map)
m

Visualizing examples of approximations and differences

In [ ]:
from turfpy.measurement import area, bbox, bbox_polygon
from turfpy.transformation import difference, convex
from geojson import Feature
from shapely.geometry import Polygon

obj = highres_data
approx = lowres_data

coordinates1 = obj['features'][0]['geometry']['coordinates'][0]
coordinates2 = approx['features'][0]['geometry']['coordinates'][0]
coordinates3 = bbox_polygon(bbox(obj))['geometry']['coordinates']
coordinates4 = convex(obj)['geometry']['coordinates']

print(coordinates1)
print(coordinates2)
print(coordinates3)
print(coordinates4)

f1= Feature(geometry=Polygon(coordinates1[0])) # object
f2= Feature(geometry=Polygon(coordinates2[0])) # low_res
f3= Feature(geometry=Polygon(coordinates3[0])) # bbox
f4= Feature(geometry=Polygon(coordinates4[0])) # convex


diff = difference(f1, f2)

geojson_1 = GeoJSON(name="High Res Polygon", data=f1, style={'color': 'blue'})

geojson_2 = GeoJSON(name='Low Res Polygon', data=f2, style={'color': 'black'})

geojson_3 = GeoJSON(name='Diff (High-Low)', data=difference(f1, f2), style={'color': 'red'})

geojson_4 = GeoJSON(name='Diff (Low-High)', data=difference(f2, f1), style={'color': 'orange'})

geojson_5 = GeoJSON(name='bbox', data=f3, style={'color': 'green'})

geojson_6 = GeoJSON(name='convex hull', data=f4, style={'color': 'yellow'})


center = [51.96954, 7.595]
m = Map(center=center, zoom=5)

m.add_layer(geojson_1)
m.add_layer(geojson_2)
m.add_layer(geojson_3)
m.add_layer(geojson_4)
m.add_layer(geojson_5)
m.add_layer(geojson_6)

control = LayersControl(position='topright')
m.add_control(control)

m

Computing the quality scores

In [ ]:
# compute the approximation quality value
def approx_quality(obj, approx):

  diff1 = difference(obj, approx)
  diff2 = difference(approx, obj)

  area_diff1 = 0
  area_diff2 = 0

  if diff1 != None:
    area_diff1 = area(diff1)

  if diff2 != None:
    area_diff2 = area(diff2)

  quality_score1 = (area(obj) + area_diff1 + area_diff2)*100 / area(obj)

  quality_score2 = (area_diff1 + area_diff2)*100 / area(obj)

  return quality_score1, quality_score2

In [ ]:
import pandas as pd

score1 = approx_quality(f1, f2)
score2 = approx_quality(f1, f3)
score3 = approx_quality(f1, f4)

data = {
  "Q1": [score1[0], score2[0], score3[0]],
  "Q2": [score1[1], score2[1], score3[1]]
}

df = pd.DataFrame(data, index = ["HighRes - LowRes", "HighRes - BBox", "HighRes - Convex"])
df

Q1         Q2
HighRes - LowRes  100.949482   0.949482
HighRes - BBox    156.033486  56.033486
HighRes - Convex  125.419152  25.419152

# Chapter 2: R-Tree

Loading and visualizing the data

In [ ]:
import requests
from turfpy.transformation import circle

url = "https://raw.githubusercontent.com/aurioldegbelo/sis2024/refs/heads/main/vector_data/geo1_example.json"

data = requests.get(url).json()

geo1 = data["features"][0]
denkpause = data["features"][1]
king_kebab = data["features"][2]
krimphove = data["features"][3]
ifgi = data["features"][4]

print(geo1)
print(denkpause)
print(king_kebab)
print(krimphove)
print(ifgi)

q_footprint = circle(ifgi, radius=80,  steps=10,  units='m') # 100, 50, 80
q_footprint['properties'] = ifgi['properties']

target_footprints = [geo1, denkpause, king_kebab, krimphove]

print(q_footprint)
print(target_footprints)

{'type': 'Feature', 'properties': {'Name': 'GEO1', 'id': 0}, 'geometry': {'coordinates': [[[7.595410964969801, 51.96985640112052], [7.595072152923166, 51.96894953936396], [7.596296431749778, 51.96883201435048], [7.596259418668183, 51.96931965343859], [7.596276501629234, 51.96956522507139], [7.596225252747445, 51.969682748162], [7.596020257222932, 51.9697827302507], [7.595410964969801, 51.96985640112052]]], 'type': 'Polygon'}}
{'type': 'Feature', 'properties': {'Name': 'Bistro Denkpause', 'id': 1}, 'geometry': {'coordinates': [[[7.59442844476078, 51.96876957052007], [7.594415375105655, 51.968695759584904], [7.5945373585494735, 51.96869039151193], [7.594480723379263, 51.96832670308601], [7.594731225092858, 51.968313282792536], [7.594837960605048, 51.96874675624372], [7.59442844476078, 51.96876957052007]]], 'type': 'Polygon'}}
{'type': 'Feature', 'properties': {'Name': 'King Kebab', 'id': 2}, 'geometry': {'coordinates': [[[7.596912214932445, 51.969501466701416], [7.596895026350126, 51.969

In [ ]:
from geojson import Point, Feature
from ipyleaflet import Map, GeoJSON, LayersControl
from turfpy.transformation import circle
from turfpy.measurement import area, bbox, bbox_polygon


center = [51.96954, 7.595]

m = Map(center=center, zoom=15)

qbbox_layer = GeoJSON(name="query bbox", data=bbox_polygon(bbox(q_footprint)), style={"color": "green"})
target_bbox_layer = GeoJSON(name = "raw data layer", data=data)

geo1_bbox_layer = GeoJSON(name = "geo1 bbox", data=bbox_polygon(bbox(geo1)) , style={"color": "red"})
denkpause_bbox_layer = GeoJSON(name = "denkpause bbox", data=bbox_polygon(bbox(denkpause)) , style={"color": "red"})
king_kebab_bbox_layer = GeoJSON(name = "king kebab bbox ", data=bbox_polygon(bbox(king_kebab)) , style={"color": "red"})
krimphove_bbox_layer = GeoJSON(name ="krimphove bbox", data=bbox_polygon(bbox(krimphove)) , style={"color": "red"})


control = LayersControl(position="topright")
m.add_control(control)

m.add_layer(target_bbox_layer)
m.add_layer(qbbox_layer)
m.add_layer(geo1_bbox_layer)
m.add_layer(denkpause_bbox_layer)
m.add_layer(king_kebab_bbox_layer)
m.add_layer(krimphove_bbox_layer)

m

In [ ]:
!pip install Rtree

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 543.2/543.2 kB 6.0 MB/s eta 0:00:00


Building the index

In [ ]:
from rtree import index

idx = index.Index()

geo1_bbox = bbox(geo1)
denkpause_bbox = bbox(denkpause)
king_kebab_bbox = bbox(king_kebab)
krimphove_bbox = bbox(krimphove)

#left, bottom, right, top = geo1_bbox

idx.insert(0, geo1_bbox)
idx.insert(1, denkpause_bbox)
idx.insert(2, king_kebab_bbox)
idx.insert(3, krimphove_bbox)

print(idx)

rtree.index.Index(bounds=[7.594415375105655, 51.968313282792536, 7.59707837122113, 51.971153993155355], size=4)


Querying the index

In [ ]:
query_window = bbox(q_footprint)

print("Intersection", list(idx.intersection(query_window)))
print("Nearest Neighbours", list(idx.nearest(query_window, 1)))

Intersection [0, 2]
Nearest Neighbours [0, 2]


In [ ]:
new_query_footprint = {
      "type": "Feature",
      "properties": {},
      "geometry": {
        "coordinates": [
          [
            [
              7.59977991078685,
              51.97186502026898
            ],
            [
              7.59977991078685,
              51.97163128236829
            ],
            [
              7.60036846588099,
              51.97163128236829
            ],
            [
              7.60036846588099,
              51.97186502026898
            ],
            [
              7.59977991078685,
              51.97186502026898
            ]
          ]
        ],
        "type": "Polygon"
  }
}

In [ ]:
from geojson import Point, Feature
from ipyleaflet import Map, GeoJSON, LayersControl
from turfpy.transformation import circle
from turfpy.measurement import area, bbox, bbox_polygon


center = [51.96954, 7.595]

m = Map(center=center, zoom=15)

qbbox_layer = GeoJSON(name="query bbox", data=bbox_polygon(bbox(new_query_footprint)), style={"color": "green"})
target_bbox_layer = GeoJSON(name = "raw data layer", data=data)

geo1_bbox_layer = GeoJSON(name = "geo1 bbox", data=bbox_polygon(bbox(geo1)) , style={"color": "red"})
denkpause_bbox_layer = GeoJSON(name = "denkpause bbox", data=bbox_polygon(bbox(denkpause)) , style={"color": "red"})
king_kebab_bbox_layer = GeoJSON(name = "king kebab bbox ", data=bbox_polygon(bbox(king_kebab)) , style={"color": "red"})
krimphove_bbox_layer = GeoJSON(name ="krimphove bbox", data=bbox_polygon(bbox(krimphove)), style={"color": "red"})
index_bounds_layer = GeoJSON(name = "index bounds", data=bbox_polygon(idx.bounds), style={"color": "orange"})

control = LayersControl(position="topright")
m.add_control(control)

m.add_layer(target_bbox_layer)
m.add_layer(qbbox_layer)
m.add_layer(geo1_bbox_layer)
m.add_layer(denkpause_bbox_layer)
m.add_layer(king_kebab_bbox_layer)
m.add_layer(krimphove_bbox_layer)
m.add_layer(index_bounds_layer)


m

In [ ]:
new_query_window = bbox(new_query_footprint)

print("Intersection", list(idx.intersection(new_query_window)))
print("Nearest Neighbours", list(idx.nearest(new_query_window,4)))

Intersection []
Nearest Neighbours [3, 2, 0, 1]
